# Here we will prepare our data to use it later in most of our models.

# Import Libraries

In [ ]:
! pip install contractions
! pip install emoji
! pip install arabic_reshaper python-bidi nltk snowballstemmer

In [ ]:
import numpy as np
import pandas as pd
pd.set_option('display.max_colwidth', None)
import plotly.express as px
import matplotlib.pyplot as plt
import tensorflow as tf

In [ ]:
from sklearn.model_selection import train_test_split
from sklearn.base import BaseEstimator, TransformerMixin
import re
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from tensorflow.keras.preprocessing.text import Tokenizer
import emoji
import arabic_reshaper
from snowballstemmer import stemmer
from sklearn.preprocessing import LabelEncoder

In [ ]:
nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\bios\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\bios\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

# Load Dataset

In [ ]:
dialects_data = pd.read_csv(r'F:\ITI Cont\NLP\Project\Dataset\dialects_data.csv', engine='python')

In [ ]:
# show the first five rows of the dataframe
dialects_data

id  \
0       1009754958479151232   
1       1009794751548313600   
2       1019989115490787200   
3       1035479791758135168   
4       1035481122921164800   
...                     ...   
147729   982775354405376000   
147730   980728852224860160   
147731   975502734668500992   
147732   980207908641263616   
147733   981080482380238848   

                                                                                                                                                                                                                                                                                                            text  \
0                                                                                                                                                                                             @toha_Altomy @gy_yah قليلين ادب ومنافقين. لو اختهم او قريبتهم تتعاكس تقولي عليهم من نشاط حقوق المرأة من ردة فعلهم.   
1                                                                                                                                                                                                                                      @AlmFaisal 😂😂 الليبيين متقلبين!!!\nبس بالنسبة ليا انا ميليشياوي زمان وتوة   
2                                                                   @smsm071990 @ALMOGRBE كل 20 تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان. بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب\nand they live happily ever after\nذي اند   
3       @AboryPro @lyranoo85 رانيا عقليتك متخلفة. اولا الانسان يلي يحتاج اهل يخاف منهم علشان يكون محترم هو انسان قليل الادب اصلاً. ثانياً شن ذنب يلي معندهش اب ولا ام ولا خوت ولا خوات؟ يعني اليتيمة متستحقش تتزوج؟ وثالثاً ليش البنت هي بس لازم ادير الف حساب للراجل؟ هي متستحقش يندارلها الف حساب ولا هي عبدة؟   
4                                                                                                                                                                                             @lyranoo85 شكلك متعقدة علشان الراجل لي تحبيه ازوج بنت يتيمة ولا بنت معندهش خوت. هدي اعصابك وفكينا من التخلف امتاعك   
...                                                                                                                                                                                                                                                                                                          ...   
147729                                                                                                                                              الناس دي بتنفخ في قربة مقدودة بالدارجي كده  البلد دي لو ما الكيزان ديل راحو مافي حياه شريفه في البلد دي لان سبب الفساد والمصائب الموجودة #التطلع_لسودان_افضل   
147730                                                                                                                                                                                                                                   @Wail_Hamza @amiromer انت عايش وين بره السودان ولا شنو ماشايف البحصل دا   
147731                                                                                                                                                                                                                                                     مااحرم نفسي ميسي حريف ولعاب برضو ..\nمدريدي وافتخر 🇪🇸   
147732                                                                                                                                                                                  ياخي ديل ماخلو  للشيطان وإبليس شي لكن يروحو وين من ربنا ونحن وراك وراك ياكوز ياعفن الأيام معدوده خلاص  #تعرف_علي_الكيزان   
147733                                                                                                                                                                                                                                                            @abdom

# EDA and Preprocessing


In [ ]:
dialects_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 147734 entries, 0 to 147733
Data columns (total 3 columns):
 #   Column   Non-Null Count   Dtype 
---  ------   --------------   ----- 
 0   id       147734 non-null  object
 1   text     147732 non-null  object
 2   dialect  147718 non-null  object
dtypes: object(3)
memory usage: 3.4+ MB


## check NaNs

In [ ]:
dialects_data.isna().sum()

id          0
text        2
dialect    16
dtype: int64

**we will delete rows with missing values**

In [ ]:
# drop rows with missing values
dialects_data = dialects_data.dropna()

In [ ]:
#check for missing values ag
dialects_data.isna().sum()

id         0
text       0
dialect    0
dtype: int64

## Check duplicates
We need drop id column before check duplicates

In [ ]:
# Drop the 'id' column
dialects_data = dialects_data.drop(columns=['id'])

In [ ]:
dialects_data.head()

text  \
0                                                                                                                                                                                        @toha_Altomy @gy_yah قليلين ادب ومنافقين. لو اختهم او قريبتهم تتعاكس تقولي عليهم من نشاط حقوق المرأة من ردة فعلهم.   
1                                                                                                                                                                                                                                 @AlmFaisal 😂😂 الليبيين متقلبين!!!\nبس بالنسبة ليا انا ميليشياوي زمان وتوة   
2                                                              @smsm071990 @ALMOGRBE كل 20 تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان. بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب\nand they live happily ever after\nذي اند   
3  @AboryPro @lyranoo85 رانيا عقليتك متخلفة. اولا الانسان يلي يحتاج اهل يخاف منهم علشان يكون محترم هو انسان قليل الادب اصلاً. ثانياً شن ذنب يلي معندهش اب ولا ام ولا خوت ولا خوات؟ يعني اليتيمة متستحقش تتزوج؟ وثالثاً ليش البنت هي بس لازم ادير الف حساب للراجل؟ هي متستحقش يندارلها الف حساب ولا هي عبدة؟   
4                                                                                                                                                                                        @lyranoo85 شكلك متعقدة علشان الراجل لي تحبيه ازوج بنت يتيمة ولا بنت معندهش خوت. هدي اعصابك وفكينا من التخلف امتاعك   

  dialect  
0      LY  
1      LY  
2      LY  
3      LY  
4      LY

In [ ]:
# Check for duplicates again after droping IDs
duplicates = dialects_data.duplicated()

# Print the number of duplicate rows
print(f"Number of duplicate rows: {duplicates.sum()}")

Number of duplicate rows: 0


## check dataset balancing

In [ ]:
# Plot the distribution of 'dialect' column with colorful bars
fig = px.histogram(dialects_data, x='dialect', color='dialect',
                   title='Distribution of Dialects',
                   labels={'dialect': 'Dialect', 'count': 'Frequency'},
                   color_discrete_sequence=px.colors.qualitative.Set1)
fig.update_xaxes(categoryorder='total descending')
fig.update_layout(xaxis_title="Dialect", yaxis_title="Frequency")
fig.show()


## **There is big imbalance here**
We Can deal with that in difference ways.

Here are a few strategies we can do to handle imbalanced datasets:

*    **Resampling Techniques:**
        Over-sampling: Increase the number of minority class samples by randomly duplicating them or generating synthetic samples (e.g., using SMOTE).
        Under-sampling: Decrease the number of majority class samples by randomly removing them.
        Combined over- and under-sampling: A combination of over-sampling the minority class and under-sampling the majority class.

*    **Algorithmic Techniques:**
        Use algorithms that are robust to class imbalance, such as tree-based algorithms (Random Forest, Gradient Boosting) or ensemble methods.
        Adjust class weights in the model to penalize misclassification of minority classes more.

*    **Evaluation Metrics:**
        Choose appropriate evaluation metrics that are less sensitive to class imbalance, such as precision, recall, F1-score.



## Show a representative sample of data texts to find out required cleaning steps.

In [ ]:
sample_data = dialects_data.sample(10)
sample_data

text  \
84029                                                                                          @Yallakoranow يبقى عايز تحلق ومكسوف\nبلاش تلاكيك يا جيمي 😉\nانت مابتحرمش ياللي مابتفمش   
33285                                                                                 @Mohamme60251932 @MahmudShammam غالط في العنوان خوي \nاللي دمر بلدك وخربها خسر امس باربعة اهداف   
71791                                                                                                                              @alkhemist64 لا حول ولا قوة الا بالله ..ربنا معاهم   
141172                                                                                                                ههههههههه والله ده أكرم سكران فى الدنيا https://t.co/XjDnMLCdYU   
57007           صاحبتي بتقولّي هاتِلبِس Skirt .. فإتكسفت أسألها إيه هو الSkirt وقولتِلها اه دا شيك فشخ .. وأنا أقسم بالله ماعرف إيه هو دا اصلاً وبيتلبِس فين 😂\n\n#عيد_الميلاد_المجيد   
93158                                                                                                                    سعودية محترمه ...تيران وصنافير مصرية https://t.co/qBQgkPJX1z   
34972   @hnanomar الله يرحمه ويغفر له ويوسع عليه بجديات\nشوفي بالرغم فارق العمر جدك الله يرحمه طلع فاهم ومتعلم خير من شباب هذاك الوقت \nوالحلو إنه خذا بخاطر بنته وما دورش كلام الناس   
61886                                                                                                                              ممكن يكون بيتعالج فى تركيا https://t.co/MJvK4lxzUO   
17410                                                                                                           اللي ايعلق علي مباراة #الميلان و #كالياري  ايخطر بيا معلق متاع #الحصن   
76816                                                                                                              @TOP_DR_ALEX9990 شادي ده واد تافه\nابن الحمضانه\nده مبلك امه نفسها   

       dialect  
84029       EG  
33285       LY  
71791       EG  
141172      SD  
57007       EG  
93158       EG  
34972       LY  
61886       EG  
17410       LY  
76816       EG

## Cleaning steps that we will need are:

- Remove Tatweel
- Remove digits and symbols
- Remove emojis
- Remove URLs
- Remove usernames
- Remove non-Arabic characters
- Remove extra spaces
- Remove hashtags
- Remove un-ASCII characters
- Handling Noise and Garbage Characters
- Handling Bi-directional Text

## Split data into features and target

In [ ]:
# Separate features (X) and target variable (y)
X_text = dialects_data['text']
y = dialects_data['dialect']

In [ ]:
label_encoder = LabelEncoder()
label_encoder.fit(y)

LabelEncoder()

In [ ]:
y = label_encoder.transform(y)

In [ ]:
y = pd.DataFrame(y, columns=['dialect'])

In [ ]:
y.shape

(147718, 1)

In [ ]:
y.value_counts()

dialect
0          57635
2          36499
1          27617
4          14433
3          11534
Name: count, dtype: int64

In [ ]:
X_text.head()

0                                                                                                                                                                                          @toha_Altomy @gy_yah قليلين ادب ومنافقين. لو اختهم او قريبتهم تتعاكس تقولي عليهم من نشاط حقوق المرأة من ردة فعلهم.
1                                                                                                                                                                                                                                   @AlmFaisal 😂😂 الليبيين متقلبين!!!\nبس بالنسبة ليا انا ميليشياوي زمان وتوة
2                                                                @smsm071990 @ALMOGRBE كل 20 تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان. بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب\nand they live happily ever after\nذي اند
3    @AboryPro @lyranoo85 رانيا عقليتك متخلفة. اولا الانسان يلي يحتاج اهل يخاف منهم علشان يكون

## Split data into train,valid and test sets

In [ ]:
X_train_valid, X_test, y_train_valid, y_test = train_test_split(X_text, y, test_size=0.2, random_state=42)

In [ ]:
X_train, X_valid, y_train, y_valid = train_test_split(X_train_valid, y_train_valid, test_size=0.25, random_state=42)

In [ ]:
X_train.shape, X_valid.shape, X_test.shape

((88630,), (29544,), (29544,))

## Define the custom transformer for Arabic text cleaning

We will use print after each steps to check the result after each step

In [ ]:
class ArabicTextCleaner(BaseEstimator, TransformerMixin):
    def __init__(self, use_stemming=False):
        self.use_stemming = use_stemming
        self.arabic_stopwords = set(stopwords.words('arabic'))

        if self.use_stemming:
            self.stemmer = stemmer("arabic")

    def fit(self, X, y=None):
        return self

    def transform(self, X, y=None):
        # If X is a single string, convert it to a list of one element
        if isinstance(X, str):
            X = [X]
        return [self.clean_text(text) for text in X]

    def clean_text(self, text):
        print("Original text:", text)

        # Removing Non-Arabic Characters
        text = re.sub(r'[^\u0600-\u06FF\s]', '', text)
        print("After removing non-Arabic characters:", text)

        # Removing Tatweel
        text = text.replace('ـ', '')
        print("After removing Tatweel:", text)

        # Removing HTML Tags
        text = re.sub(r'<.*?>', '', text)
        print("After removing HTML tags:", text)

        # Tokenization
        words = word_tokenize(text)
        print("After tokenization:", words)

        # Removing Stopwords
        words = [word for word in words if word not in self.arabic_stopwords]
        print("After removing stopwords:", words)

        # Removing Digits and Symbols
        text = re.sub(r'[0-9’!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~]+', '', ' '.join(words))
        print("After removing digits and symbols:", text)

        # Stemming
        if self.use_stemming:
            words = [self.stemmer.stemWord(word) for word in words]
        print("After stemming:", words)

        text = ' '.join(words)
        print("After joining words:", text)

        # Remove hashtag
        text = re.sub(r'#([^\s]+)', '', text)
        print("After removing hashtags:", text)

        # Removing URLs and Email Addresses and usernames
        text = re.sub(r'http\S+|www\S+|@\S+', '', text)
        print("After removing URLs and usernames:", text)

        # Removing Emojis and Symbols
        text = ''.join(char for char in text if not emoji.is_emoji(char))

        print("After removing emojis and symbols:", text)

        # Removing Repeated Characters
        text = re.sub(r'(.)\1{2,}', r'\1\1', text)
        print("After removing repeated characters:", text)

        # Handling Noise and Garbage Characters
        text = re.sub(r'[^\u0600-\u06FF\s]', '', text)  # Removing non-Arabic characters again
        print("After handling noise and garbage characters:", text)

        return text

In [ ]:
# Try the ArabicTextCleaner class on the sample data
n="@smsm071990 @ALMOGRBE ♥️😂🥰👩🏻‍💻❎✅ كل 20 تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان. بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب\nand they live happily ever after\nذي اند	"
cleaning = ArabicTextCleaner()
cleaned_n = cleaning.transform(n)
print(cleaned_n)

Original text: @smsm071990 @ALMOGRBE ♥️😂🥰👩🏻‍💻❎✅ كل 20 تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان. بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب
and they live happily ever after
ذي اند	
After removing non-Arabic characters:    كل  تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب
     
ذي اند	
After removing Tatweel:    كل  تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب
     
ذي اند	
After removing HTML tags:    كل  تانيه شاب ليبي بيرتاح لبنت مختلفة ويلاحظ انها غير كل البنات وبيحس كأنه يعرفها من زمان بعدين يتزوج وحدة منهن وممكن اثنين ولاثلاثة وتنقلب الرومانسية لعياط وشياط وتهزيب
     
ذي اند	
After tokenization: ['كل', 'تانيه', 'شاب', 'ليبي', 'بيرتاح', 'لبنت', 'مختلفة', 'ويلاحظ', 

In [ ]:
class ArabicTextCleaner(BaseEstimator, TransformerMixin):
    def __init__(self, use_stemming=False):
        self.use_stemming = use_stemming
        self.arabic_stopwords = set(stopwords.words('arabic'))

        if self.use_stemming:
            self.stemmer = stemmer("arabic")

    def fit(self, X, y=None):
        return self

    def transform(self, X, y=None):
        # If X is a single string, convert it to a list of one element
        if isinstance(X, str):
            X = [X]
        return [self.clean_text(text) for text in X]

    def clean_text(self, text):

        # Removing Non-Arabic Characters
        text = re.sub(r'[^\u0600-\u06FF\s]', '', text)


        # Removing Tatweel
        text = text.replace('ـ', '')

        # Removing HTML Tags
        text = re.sub(r'<.*?>', '', text)

        # Tokenization
        words = word_tokenize(text)



        # Removing Digits and Symbols
        text = re.sub(r'[0-9’!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~]+', '', ' '.join(words))

        # Stemming
        if self.use_stemming:
            words = [self.stemmer.stemWord(word) for word in words]

        text = ' '.join(words)


        # Remove hashtag
        text = re.sub(r'#([^\s]+)', '', text)

        # Removing URLs and Email Addresses and usernames
        text = re.sub(r'http\S+|www\S+|@\S+', '', text)


        # Removing Emojis and Symbols
        text = ''.join(char for char in text if not emoji.is_emoji(char))

        # Removing Repeated Characters
        text = re.sub(r'(.)\1{2,}', r'\1\1', text)

        # Handling Noise and Garbage Characters
        text = re.sub(r'[^\u0600-\u06FF\s]', '', text)

        return text

This is the time for using transform to clean our data

In [ ]:
cleaning = ArabicTextCleaner()
cleaned_x_train = cleaning.transform(X_train)
cleaned_x_train[0]

'اي خبر او تطور من جل الديب حدا يدقلي ما بفتحلو خط ح اغفى شوي'

In [ ]:
cleaned_x_valid = cleaning.transform(X_valid)
cleaned_x_test = cleaning.transform(X_test)

# Save the cleaned data to CSV files to use it later in modeling.

In [ ]:
# Combine the transformed data and labels into DataFrames
df_cleaned_x_test = pd.DataFrame({'cleaned_x_test': cleaned_x_test, 'y_test':y_test.squeeze()})
df_cleaned_x_train = pd.DataFrame({'cleaned_x_train': cleaned_x_train, 'y_train':y_train.squeeze()})
df_cleaned_x_valid = pd.DataFrame({'cleaned_x_valid': cleaned_x_valid, 'y_valid':y_valid.squeeze()})

In [ ]:
# Save the DataFrames to CSV files
df_cleaned_x_train.to_csv('cleaned_x_train.csv', index=False)
df_cleaned_x_valid.to_csv('cleaned_x_valid.csv', index=False)
df_cleaned_x_test.to_csv('cleaned_x_test.csv', index=False)

# Tokenization

In [ ]:
class CustomTokenizer(BaseEstimator, TransformerMixin):
    def __init__(self):

        self.tokenizer = Tokenizer()

    def fit(self, X, y=None):
        # Fit the tokenizer on the input text
        self.tokenizer.fit_on_texts(X)
        return self

    def transform(self, X, y=None):

        # Tokenize the input text into sequences of tokens
        sequences = self.tokenizer.texts_to_sequences(X)
        return sequences

In [ ]:
# Instantiate an object of the CustomTokenizer class
tokenizer = CustomTokenizer()

# Fit the tokenizer on the training data
xtrain_tokens=tokenizer.fit(cleaned_x_train )

x_train_idx = tokenizer.transform(cleaned_x_train)
x_train_idx[0]

[53, 598, 40, 4565, 1, 9495, 7404, 111, 43667, 3, 68138, 1099, 325, 43668, 293]

In [ ]:
x_valid_idx = tokenizer.transform(cleaned_x_valid)
x_test_idx = tokenizer.transform(cleaned_x_test)

# Calculate max lenth for sentence and determine VOCAB SIZE

In [ ]:
max_sequence_len = 0
for sentence in X_train:
    max_sequence_len = max(len(sentence), max_sequence_len)
print(max_sequence_len)

698


In [ ]:
import plotly.express as px

# Calculate lengths of sentences in x_train
sentence_lengths = [len(sentence) for sentence in x_train_idx]

# Create histogram figure using Plotly Express
fig = px.histogram(x=sentence_lengths, title='Distribution of Sentence Lengths in x_train_idx',
                   labels={'x': 'Sentence Length', 'y': 'Frequency'})

fig.show()

According to to the Distribution of Sentence Lengths in x_train we will
set **max_length to 50**.

In [ ]:
max_sequence_len = 50

In [ ]:
# Extract unique tokens from the tokenized sequences
unique_tokens = set(token for sequence in x_train_idx for token in sequence)

In [ ]:
# Calculate the vocabulary size based on the number of unique tokens
VOCAB_SIZE = len(unique_tokens)+10
print("Vocabulary Size:", VOCAB_SIZE)

Vocabulary Size: 187686


# Padding
**Pad sequences to ensure uniform input size for the RNN. This step is crucial because RNNs require input sequences of the same length.**

In [ ]:
class padding(BaseEstimator, TransformerMixin):
    def __init__(self, max_sequence_len):

        self.max_sequence_len = max_sequence_len

    def fit(self, X, y=None):

        return self

    def transform(self, X):

        # Initialize the padded dataset with zeros
        X_padded = np.zeros((len(X), max_sequence_len))

        # Pad each sequence
        for i, sent in enumerate(X):
            X_padded[i, :min(len(sent), self.max_sequence_len)] = sent[:self.max_sequence_len]

        return X_padded

In [ ]:
pt=padding(max_sequence_len)
x_train_padded =pt.fit_transform(x_train_idx)
x_valid_padded =pt.fit_transform(x_valid_idx)
x_test_padded =pt.fit_transform(x_test_idx)

In [ ]:
x_train_padded[0]

array([5.3000e+01, 5.9800e+02, 4.0000e+01, 4.5650e+03, 1.0000e+00,
       9.4950e+03, 7.4040e+03, 1.1100e+02, 4.3667e+04, 3.0000e+00,
       6.8138e+04, 1.0990e+03, 3.2500e+02, 4.3668e+04, 2.9300e+02,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
       0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00])

# Save the padded data to CSV files to use it later in modeling.

In [ ]:
# Create DataFrames from the padded sequences
df_x_train_padded = pd.DataFrame(x_train_padded)
df_x_valid_padded = pd.DataFrame(x_valid_padded)
df_x_test_padded = pd.DataFrame(x_test_padded)

In [ ]:
df_x_test_padded = pd.DataFrame(x_test_padded)

In [ ]:
# Add the labels to the DataFrames
df_x_train_padded['y_train'] = y_train.values
df_x_valid_padded['y_valid'] = y_valid.values
df_x_test_padded['y_test'] = y_test.values


In [ ]:
# Save the DataFrames to CSV files
df_x_train_padded.to_csv('x_train_padded.csv', index=False)
df_x_valid_padded.to_csv('x_valid_padded.csv', index=False)
df_x_test_padded.to_csv('x_test_padded.csv', index=False)